# Transformer architecture

In [1]:
!pip install bertviz

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 157.6/157.6 kB 7.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.0/11.0 MB 48.0 MB/s eta 0:00:00
  Attempting uninstall: botocore
    Found existing installation: botocore 1.34.131
    Uninstalling botocore-1.34.131:
      Successfully uninstalled botocore-1.34.131
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
aiobotocore 2.13.2 requires botocore<1.34.132,>=1.34.70, but you have botocore 1.29.165 which is incompatible.


In [2]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from transformers import AutoTokenizer, AutoConfig, AutoModel
from bertviz.transformers_neuron_view import BertModel
from bertviz.neuron_view import show
from bertviz import head_view
from math import sqrt

# Transformer Encoder

**Transformer Encoder** — bu Transformer arxitekturasining asosiy qismi bo'lib, ma'lumotlarni kirish (input) dan olish va ularni chuqur o'rgangan (learned) vakillar (representations) sifatida chiqarish uchun ishlatiladi. Bu arxitektura tabiiy tilni qayta ishlash (NLP), masalan, tarjima, matn tasnifi, savol-javob tizimlari kabi vazifalarda keng qo'llaniladi.

### Transformer Encoder nima?

Transformer Encoder — bu bir nechta qatlamlardan iborat model, har bir qatlam o'z ichida ikkita asosiy komponentni o'z ichiga oladi:

- **Self-Attention Layer (o'zaro e'tibor qatlamlari)**
- **Feed-Forward Neural Network Layer (oldinga o'tkazuvchi neyron tarmoq qatlamlari)**

Har bir qatlamda kirish ma'lumotlari e'tibor mexanizmi orqali qayta ishlanadi va keyin neyron tarmoq orqali o'tadi. Bu qatlamlar ko'p martalab ishlatiladi (bir nechta qatlamlar qo'llaniladi) va natijada kirish ma'lumotlari chuqurroq va boyroq vakilliklarga aylanadi.

### Transformer Encoder qanday ishlaydi?

Oddiy qilib aytganda, Transformer Encoder quyidagi bosqichlarda ishlaydi:

1. **Kirish (Input):**
   - Dastlab, matn yoki ma'lumotlar vektor ko'rinishiga o'tkaziladi. Bu jarayon token embedding yordamida amalga oshiriladi, va pozitsion embeddinglar qo'shiladi.

2. **Self-Attention Layer:**
   - Bu qatlam kirish ma'lumotlarining har bir qismini (masalan, har bir so'z yoki tokenni) qolgan qismlariga e'tibor qaratishga imkon beradi. Bu jarayon orqali model har bir so'zning boshqa so'zlar bilan qanday bog'liq ekanligini o'rganadi. Masalan, "mushuk" so'zi jumladagi "sut ichdi" bilan bog'liq bo'lishi mumkin, shuning uchun "mushuk" so'zi e'tibor mexanizmi yordamida "sut" va "ichdi" so'zlariga bog'lanadi.

3. **Feed-Forward Neural Network Layer:**
   - Self-Attention Layer orqali olingan ma'lumotlar keyinroq oldinga o'tkazuvchi neyron tarmoq qatlamlari orqali qayta ishlanadi. Bu qatlam ma'lumotni chuqurroq o'rganib, yanada boy vakillarni hosil qiladi.

4. **Skip Connections va Layer Normalization:**
   - Har bir qatlamda kirish va chiqish ma'lumotlari o'rtasida "skip connections" (uzatma bog'lanishlar) qo'shiladi, bu esa o'qitishni barqaror qiladi. Shuningdek, layer normalization (qatlamni normallashtirish) texnikasi yordamida ma'lumotlar o'rtacha qiymatga keltiriladi, bu modelning samarali ishlashiga yordam beradi.

5. **Natija:**
   - Eng oxirida, Encoder tomonidan qayta ishlangan ma'lumotlar chiqariladi. Bu ma'lumotlar asosan kirish matnining chuqur va kontekstual vakillari bo'lib, ular keyingi bosqichlarda, masalan, dekoder qismi yoki klassifikatsiya uchun ishlatilishi mumkin.

### Transformer Encoderning vazifasi nima?

Transformer Encoderning asosiy vazifasi — kirish ma'lumotlarini (masalan, matnni) chuqur va boy vakilliklarga aylantirish. Bu vakilliklar kirish ma'lumotlarining turli qismlarini bir-biri bilan bog'lash va ularning kontekstual ma'nosini yaxshiroq tushunishga imkon beradi. Transformer Encoder modullari tabiiy tilni qayta ishlash jarayonida quyidagi vazifalarni bajaradi:

- **Matn tushunish:** Kirish matnining kontekstini chuqurroq tushunadi va ma'lumotlarning qanday bog'liqligini o'rganadi.
- **Xotira (Memory):** Model har bir so'zning yoki tokenning kontekstual ma'nosini eslab qoladi va boshqa tokenlar bilan qanday bog'liqligini o'rganadi.
- **Ma'lumotni boyitish:** Matndagi har bir so'zning ma'nosini kontekst orqali boyitadi va bu vakilliklarni yanada aniqroq qiladi.
- **Natijaga tayyorlash:** Ushbu vakilliklar keyingi bosqichlar (masalan, dekoder yoki klassifikator) uchun ishlatiladigan ma'lumotlar sifatida xizmat qiladi.

Transformer Encoder matnning kontekstual tushunchasini hosil qiladigan va turli so'zlar orasidagi aloqalarni o'rganadigan kuchli komponentdir. Bu jarayon tabiiy tilni qayta ishlash vazifalarida aniq va samarali natijalar beradi.


In [3]:
model_ckpt = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

/opt/conda/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [4]:
model = BertModel.from_pretrained(model_ckpt)

100%|██████████| 440473133/440473133 [00:16<00:00, 26460605.38B/s]
/opt/conda/lib/python3.10/site-packages/bertviz/transformers_neuron_view/modeling_utils.py:482: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues rela

## Self-Attention

**Self-Attention** — bu Transformer arxitekturasining markaziy mexanizmi bo'lib, u kirish ma'lumotlarining har bir qismini (masalan, so'z yoki token) qolgan qismlarga e'tibor qaratishga imkon beradi. Bu jarayon orqali model kirish ma'lumotlaridagi barcha elementlar o'rtasidagi bog'liqlikni o'rganadi va har bir elementning kontekstual ma'nosini chuqurroq tushunishga yordam beradi.

### Self-Attentionning vazifasi nima?

Self-Attentionning asosiy vazifasi — kirish ma'lumotlari orasidagi bog'lanishlarni topish va har bir elementning qolgan elementlar bilan qanday bog'liq ekanligini o'rganish. Bu vazifa tilni qayta ishlashda juda muhim, chunki so'zlarning ma'nosi ko'pincha ularning kontekstiga bog'liq bo'ladi. Self-Attention bu bog'lanishlarni hisobga olib, har bir so'zning ahamiyatini aniqlaydi va kontekstual vakilliklarni hosil qiladi.

Masalan, "Mushuk sut ichdi" jumlasini olaylik. Bu jumlada "sut ichdi" qismi "mushuk" bilan bog'liq. Self-Attention mexanizmi "sut" va "ichdi" so'zlarining "mushuk" bilan qanday bog'liqligini aniqlaydi va o'zaro bog'lanishlarni yaratadi.

### Self-Attention qanday ishlaydi?

Self-Attention jarayoni bir nechta bosqichlardan iborat:

1. **Kirish vektorlarini yaratish (Q, K, V):**

   Kirish ma'lumotlari uch xil vektorga bo'linadi:
   - **Query (Q)**: So'z yoki tokenning ma'lumotni qidirish jarayonida ishlatiladigan vektori.
   - **Key (K)**: Ma'lumotni qidirishda foydalaniladigan kalit vektor.
   - **Value (V)**: Kalit bilan bog'liq bo'lgan qiymat vektori.
   
   Har bir so'z uchun Q, K, va V vektorlar alohida hisoblanadi.

2. **E'tibor skorlarini hisoblash:**

   Har bir so'z uchun Query vektori boshqa so'zlarning Key vektorlari bilan o'zaro skalar ko'paytma orqali baholanadi. Bu baholar har bir so'zning boshqa so'zlar bilan bog'liqlik darajasini ifodalaydi.
   
   Baholarni hisoblash formulasi:
   
   $$ \text{Attention}(Q, K) = \frac{Q \cdot K^T}{\sqrt{d_k}} $$
   
   Bu yerda \( d_k \) — Key vektorining o'lchami, bu normalizatsiya uchun ishlatiladi.

3. **Softmax funktsiyasi:**

   Hisoblangan e'tibor skorlari Softmax funktsiyasi yordamida normalizatsiya qilinadi. Natijada, har bir so'zning boshqa so'zlar bilan bog'liqlik ehtimoli olinadi.

4. **Yakuniy qiymatlarni olish:**

   E'tibor ehtimolliklari Value vektorlariga qo'llaniladi. Ya'ni, Value vektorlar e'tibor skorlari yordamida vaznlantiriladi. Natijada, har bir so'z uchun o'zining va boshqa so'zlarning kontekstual vakili hosil qilinadi.

5. **Chiqish vektorini hosil qilish:**

   Yakuniy qiymatlar yig'ilib, har bir so'zning kontekstual vakili hosil qilinadi. Bu vektorlar keyingi qatlamlarga yoki dekoder qismiga uzatiladi.


In [5]:
text = "time files like an arrow"

In [6]:
show(model, "bert", tokenizer, text, display_mode="light", layer=0, head=8)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [7]:
inputs = tokenizer(text, return_tensors="pt", add_special_tokens=False)
inputs.input_ids

tensor([[2051, 6764, 2066, 2019, 8612]])

In [8]:
text

'time files like an arrow'

In [9]:
show(model, "bert", tokenizer, text, display_mode="light", layer=0, head=8)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [10]:
config = AutoConfig.from_pretrained(model_ckpt)
token_emb = nn.Embedding(config.vocab_size, config.hidden_size)
token_emb

Embedding(30522, 768)

In [11]:
input_embeds = token_emb(inputs.input_ids)
input_embeds.size()

torch.Size([1, 5, 768])

In [12]:
query = key = value = input_embeds
dim_k = key.size(-1)

In [13]:
dim_k

768

In [14]:
key.shape

torch.Size([1, 5, 768])

In [15]:
key.transpose(1,2).shape

torch.Size([1, 768, 5])

In [16]:
scores = torch.bmm(query, key.transpose(1,2)) / sqrt(dim_k)
scores.size()

torch.Size([1, 5, 5])

In [17]:
weights = F.softmax(scores, dim=-1)
weights.sum(dim=-1)

tensor([[1., 1., 1., 1., 1.]], grad_fn=<SumBackward1>)

In [18]:
attn_outputs = torch.bmm(weights, value)
attn_outputs.shape

torch.Size([1, 5, 768])

In [19]:
def scaled_dot_product_attention(query, key, value):
    dim_k = query.size(-1)
    scores = torch.bmm(query, key.transpose(1,2))/dim_k ** 0.5 
    weights = F.softmax(scores, dim=-1)
    return torch.bmm(weights, value)

In [20]:
scaled_dot_product_attention(query, key, value).shape

torch.Size([1, 5, 768])

## Multi-Head Attention

**Multi-Head Attention** — bu Transformer arxitekturasidagi asosiy mexanizmlardan biri bo'lib, self-attention mexanizmini bir nechta "boshlik" (head) yordamida parallel ravishda amalga oshirish orqali ma'lumotni yanada boyroq va ko'p qirrali vakillikda olish imkonini beradi.

### Multi-Head Attentionning vazifasi nima?

Multi-Head Attentionning asosiy vazifasi — self-attentionni bir nechta turli "ko'rinishlarda" bajarish orqali ma'lumotning turli kontekstlarini bir vaqtning o'zida o'rganish. Bu turli e'tibor "boshliqlari" kirish ma'lumotlarini turli fazoviy va semantik o'lchamlarda o'rganishga imkon beradi.

Masalan, bir bosh self-attention jarayonida jumladagi so'zlarning yaqin semantik bog'liqliklarini o'rganishi mumkin bo'lsa, boshqa bosh jumladagi uzoq masofadagi so'zlar o'rtasidagi bog'lanishlarni o'rganishi mumkin. Multi-Head Attention bu boshlarning natijalarini birlashtirib, yanada boy va ko'p qirrali vakillikni hosil qiladi.

### Multi-Head Attention qanday ishlaydi?

Multi-Head Attention quyidagi bosqichlarda ishlaydi:

1. **Input (Kirish ma'lumotlari)**:

   Modelga kirish sifatida **Q** (Query), **K** (Key), va **V** (Value) vektorlar beriladi. Bu vektorlar odatda token embeddinglar va positional embeddinglardan hosil qilinadi.

2. **Vektorlarga boshliqlar yaratish (Heads)**:

   Kirish vektorlari bir nechta boshliqlarga bo'linadi. Har bir bosh o'zining **Q**, **K** va **V** vektorlarini yaratadi. Bu vektorlar kichikroq o'lchamli bo'lib, har bir bosh kirish ma'lumotlarining turli o'lchamlarini o'rganishga imkon beradi. Agar **d_model** umumiy o'lcham bo'lsa va **h** boshliqlar soni bo'lsa, har bir bosh uchun vektorlarning o'lchami **d_k = d_model / h** bo'ladi.

3. **Self-Attentionni hisoblash**:

   Har bir boshda self-attention alohida hisoblanadi. Ya'ni, har bir bosh uchun Attention(Q, K, V) formula ishlaydi:
   $$
   \text{Attention}(Q, K, V) = \text{Softmax}\left(\frac{Q \cdot K^T}{\sqrt{d_k}}\right) \cdot V
   $$
   Bu yerda, har bir bosh uchun o'zining e'tibor skorlari hisoblanadi va o'zining qiymatlari (Values) vaznlantiriladi.

4. **Boshliqlarni birlashtirish (Concatenation)**:

   Har bir boshning chiqishlari birlashtiriladi (concatenation). Bu jarayon orqali har bir boshdan olingan vakilliklar bir butun holatda yig'iladi.

5. **Chiqishni yakuniy ishlov berish (Output Projection)**:

   Birlashtirilgan natija yakuniy linear qatlam (projection layer) orqali o'zgaradi va modelning keyingi qismiga uzatiladi. Bu bosqichda o'lcham **d_model** ga qaytariladi.


In [21]:
class AttentionHead(nn.Module):
    def __init__(self, embed_dim, head_dim):
        super().__init__()
        self.q = nn.Linear(embed_dim, head_dim)
        self.k = nn.Linear(embed_dim, head_dim)
        self.v = nn.Linear(embed_dim, head_dim)
        
    def forward(self, hidden_state):
        attn_outputs = scaled_dot_product_attention(
            self.q(hidden_state), self.k(hidden_state), self.v(hidden_state)
        )
        return attn_outputs

In [22]:
class MultiHeadAttention(nn.Module):
    def __init__(self, config):
        super().__init__()
        embed_dim = config.hidden_size
        num_heads = config.num_attention_heads
        head_dim = embed_dim//num_heads
        self.heads = nn.ModuleList(
            [AttentionHead(embed_dim, head_dim) for _ in range(num_heads)]
        )
        self.output_linear = nn.Linear(embed_dim, embed_dim)
        
    def forward(self, hidden_state):
        x = torch.cat([h(hidden_state) for h in self.heads], dim=-1)
        x = self.output_linear(x)
        return x

In [23]:
multihead_attn = MultiHeadAttention(config)

In [24]:
attn_output = multihead_attn(input_embeds)
attn_output.size()

torch.Size([1, 5, 768])

In [25]:
model = AutoModel.from_pretrained(model_ckpt, output_attentions=True)

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

In [26]:
sentence_a = "time flies like an arrow"
sentence_b = "fruit flies like a banana"

In [27]:
viz_inputs = tokenizer(sentence_a, sentence_b, return_tensors = "pt")

In [28]:
attention = model(**viz_inputs).attentions

BertSdpaSelfAttention is used but `torch.nn.functional.scaled_dot_product_attention` does not support non-absolute `position_embedding_type` or `output_attentions=True` or `head_mask`. Falling back to the manual attention implementation, but specifying the manual implementation will be required from Transformers version v5.0.0 onwards. This warning can be removed using the argument `attn_implementation="eager"` when loading the model.


In [29]:
sentence_b_start = (viz_inputs.token_type_ids == 0).sum(dim=1)
tokens = tokenizer.convert_ids_to_tokens(viz_inputs.input_ids[0])

In [30]:
head_view(attention, tokens, sentence_b_start, heads=[8])

<IPython.core.display.Javascript object>

## Feed Forward Layer

**Feed Forward Layer** Transformer arxitekturasidagi asosiy komponentlardan biridir. Bu qatlam har bir tokenning vakilligini mustaqil tarzda qayta ishlaydi va ko'proq murakkablik va kuch ko'rsatish imkonini beradi. 

### Feed Forward Layerning vazifasi nima?

Feed Forward Layerning asosiy vazifasi — ma'lumotlarni keyingi qatlamlarga uzatishdan oldin, har bir token uchun muayyan hisoblashlarni bajarish. Bu qatlam har bir tokenning vakilligini alohida-alohida qayta ishlaydi va natijada ko'proq murakkab xususiyatlarni o'rganish imkonini beradi.

### Feed Forward Layer qanday ishlaydi?

Feed Forward Layer ikki qismdan iborat bo'lib, quyidagi bosqichlarda ishlaydi:

1. **Kirish ma'lumotlari**:

   Modelga kirish sifatida token embeddinglari yoki self-attention qatlamidan chiqish ma'lumotlari beriladi. 

2. **Birlamchi Linear Qatlam**:

   Kirish ma'lumotlari birinchi linear qatlamdan o'tadi. Bu qatlam kirish vektorlarini yuqori o'lchamli fazoviy vakilliklarga o'tkazadi. Agar **d_model** kirish o'lchami bo'lsa va **d_ff** yashirin qatlam o'lchami bo'lsa, birinchi linear qatlamda quyidagi formula ishlatiladi:
   $$
   \text{Intermediate} = \text{Linear}_1(x)
   $$
   
3. **Aktivatsiya Funktsiyasi**:

   Birlamchi linear qatlamdan olingan natija aktivatsiya funktsiyasidan o'tadi. Ko'pincha, **GELU** yoki **ReLU** aktivatsiya funktsiyalari ishlatiladi:
   $$
   \text{Activated} = \text{Activation}(\text{Intermediate})
   $$

4. **Ikkinchi Linear Qatlam**:

   Aktivatsiya funktsiyasidan o'tgan natija ikkinchi linear qatlamdan o'tadi. Bu qatlamni yakuniy o'lchamga (ya'ni, **d_model**) qaytaradi:
   $$
   \text{Output} = \text{Linear}_2(\text{Activated})
   $$

5. **Dropout**:

   Modelning ortiqcha moslashuvchanligini kamaytirish uchun dropout qatlamidan o'tishi mumkin. Bu qatlam neyronlar bilan tasodifiy tanlanadi va ularni trening vaqtida o'chirib qo'yadi.

6. **Chiqish**:

   Yakuniy natija, ya'ni **Output**, keyingi qatlamlarga uzatiladi.

### Misol

Aytaylik, sizning modelingizda bir token uchun quyidagi ma'lumotlar mavjud:

- Kirish: $x = [x_1, x_2, ..., x_n]$
- Yashirin qatlam o'lchami: $d_{ff} = 4 \times d_{model}$

Kirish ma'lumotlari avval birinchi linear qatlamdan o'tadi, so'ngra aktivatsiya funktsiyasidan o'tadi, ikkinchi linear qatlamdan o'tadi va natijada yakuniy output hosil qilinadi.

### Xulosa

Feed Forward Layer Transformer arxitekturasida har bir tokenning vakilligini mustaqil ravishda qayta ishlash uchun ishlatiladi. Bu qatlam ko'proq murakkablik va kuch ko'rsatish imkonini beradi, shuningdek, ma'lumotlarning yuqori darajadagi vakilliklarini yaratadi.


In [31]:
class FeedForward(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.linear_1 = nn.Linear(config.hidden_size, config.intermediate_size)
        self.linear_2 = nn.Linear(config.intermediate_size, config.hidden_size)
        self.gelu = nn.GELU()
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        
    def forward(self, x):
        x = self.linear_1(x)
        x = self.gelu(x)
        x = self.linear_2(x)
        x = self.dropout(x)
        return x

In [32]:
feed_forward = FeedForward(config)
ff_outputs = feed_forward(attn_outputs)
ff_outputs.size()

torch.Size([1, 5, 768])

## Layer Normalization

**Layer Normalization** — bu neyron tarmoqlarda ma'lumotlarning tarqatilishini normallashtirish uchun ishlatiladigan texnikadir. U modelning o'qishini barqarorlashtirish va tezlashtirish uchun muhim ahamiyatga ega.

### Layer Normalizationning vazifasi nima?

Layer Normalizationning asosiy vazifasi — har bir layerdagi xususiyatlarning tarqatilishini normallashtirish orqali o'quv jarayonini yaxshilash. Bu normallashtirish jarayoni modelni barqarorlashtiradi va gradientlarning o'zgarishini kamaytiradi, shuningdek, tezroq konvergensiya va yaxshiroq natijalarni ta'minlaydi.

### Layer Normalization qanday ishlaydi?

Layer Normalization quyidagi bosqichlarda ishlaydi:

1. **Kirish Ma'lumotlari**:

   Har bir tokenning vakilligi, ya'ni xususiyatlar vektori, **Layer Normalization** qatlamiga uzatiladi. Faraz qilaylik, bu vektor **x** deb ataladi va o'lchami **d** bo'lishi mumkin.

2. **Orta va Standart Og'ish Hisoblash**:

   Layer Normalization, har bir xususiyat uchun o'rtacha qiymat (mean) va standart og'ish (standard deviation) hisoblaydi:
   $$
   \text{mean} = \frac{1}{d} \sum_{i=1}^d x_i
   $$
   $$
   \text{std} = \sqrt{\frac{1}{d} \sum_{i=1}^d (x_i - \text{mean})^2}
   $$

3. **Normallashtirish**:

   Ma'lumotlar normallashtiriladi. Har bir element uchun o'rtacha qiymat va standart og'ish ishlatiladi:
   $$
   \hat{x}_i = \frac{x_i - \text{mean}}{\text{std} + \epsilon}
   $$
   Bu yerda, $\epsilon$ — numerik barqarorlik uchun kichik bir qiymat.

4. **O'lchamlarni O'zgartirish va Qiymatlarni Yig'ish**:

   Normallashtirilgan ma'lumotlar, modelning o'qitilishi uchun optimal holatda bo'lishi uchun o'lchamlar va qiymatlarni yig'ish (scale) va o'zgartirish (shift) orqali o'zgartiriladi:
   $$
   \text{Output} = \gamma \cdot \hat{x} + \beta
   $$
   Bu yerda, $\gamma$ (scale) va $\beta$ (shift) o'qitiladigan parametrlar bo'lib, modelning o'zgaruvchanliklarini saqlab qoladi.

### Misol

Aytaylik, sizning bir qatlamdagi kirish vektoringiz $x = [2.0, 0.0, 1.0]$. Bu vektor uchun Layer Normalization quyidagi bosqichlarda ishlaydi:

1. **Orta va Standart Og'ish**:
   - $\text{mean} = \frac{2.0 + 0.0 + 1.0}{3} = 1.0$
   - $\text{std} = \sqrt{\frac{(2.0 - 1.0)^2 + (0.0 - 1.0)^2 + (1.0 - 1.0)^2}{3}} = 0.816$

2. **Normallashtirish**:
   - $\hat{x}_1 = \frac{2.0 - 1.0}{0.816} = 1.224$
   - $\hat{x}_2 = \frac{0.0 - 1.0}{0.816} = -1.224$
   - $\hat{x}_3 = \frac{1.0 - 1.0}{0.816} = 0.0$

3. **O'lchamlarni O'zgartirish va Qiymatlarni Yig'ish**:
   - Misol uchun, $\gamma = 1.0$ va $\beta = 0.0$ bo'lsa, natija shunchaki normallashtirilgan qiymat bo'ladi: $[1.224, -1.224, 0.0]$.

### Xulosa

Layer Normalization neyron tarmoqlarda ma'lumotlarni normallashtirish orqali o'qitish jarayonini barqarorlashtiradi va tezlashtiradi. Bu metod, modelning o'qishini yaxshilash va natijalarni yaxshilash uchun juda muhimdir.


In [33]:
class TransformerEncoderLayer(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.layer_norm_1 = nn.LayerNorm(config.hidden_size)
        self.layer_norm_2 = nn.LayerNorm(config.hidden_size)
        self.attention = MultiHeadAttention(config)
        self.feed_forward = FeedForward(config)
        
    def forward(self, x):
        hidden_state = self.layer_norm_1(x)
        x = x +  self.attention(hidden_state)
        x = x + self.feed_forward(self.layer_norm_2(x))
        return x

In [34]:
encoder_layer = TransformerEncoderLayer(config)
input_embeds.shape, encoder_layer(input_embeds).size()

(torch.Size([1, 5, 768]), torch.Size([1, 5, 768]))

## Token va Position Embeddinglar

**Embedding** — bu so'z yoki belgilarni raqamli shaklga (vektorlarga) o'tkazish jarayonidir. Neyron tarmoqlarda bu jarayon so'zlar yoki tokenlar orasidagi semantik aloqalarni ifodalash uchun ishlatiladi. Vektorlar neyron tarmoqda kirish sifatida ishlatiladigan raqamli ifodalardir.

### Token Embedding nima?

**Token embedding** — bu modelga kiruvchi so'zlarni yoki belgilarni vektorga o'tkazish jarayonidir. Har bir so'z yoki belgiga (token) o'ziga xos vektor mos keladi. Bu vektorlar odatda turli o'lchamlarda bo'lib, modelni o'rganish jarayonida o'zgaradi.

Misol uchun, so'zlarni vektorlar shaklida quyidagicha ifodalash mumkin:

- "Mushuk" -> [0.1, 0.8, -0.2]
- "It" -> [0.2, 0.9, -0.3]

Bu vektorlar so'zlarning semantik (ma'no jihatdan) yaqinligini ifodalaydi. Masalan, "mushuk" va "it" vektorlarining o'xshash bo'lishi ularning ma'no jihatdan bir-biriga yaqin ekanligini bildiradi.

Token embeddinglar o'qitiladigan va model tomonidan o'rganiladigan qatlam bo'lib, neyron tarmoqka kiritilgan so'zlar yoki tokenlar asosida o'zgaradi.

### Position Embedding nima?

**Position embedding** — bu transformer arxitekturasida so'zlarning ketma-ketlikdagi pozitsiyalarini ifodalash uchun ishlatiladigan texnika. Transformer modelida, ayniqsa self-attention mexanizmidan foydalanganda, so'zlarning pozitsion ma'lumotlari muhim rol o'ynaydi. Chunki model so'zlarning o'zaro bog'liqligini o'rganishi uchun ularning ketma-ketlikdagi o'rnini bilishi kerak.

Position embeddinglar har bir pozitsiyaga mos keladigan vektorlarni hosil qiladi. Masalan, birinchi, ikkinchi yoki uchinchi so'zlar uchun turli pozitsion vektorlar tayinlanadi. Bu vektorlar token embeddinglariga qo'shiladi, shunda model so'zlarning o'rnini ham hisobga oladi.

Misol uchun:

- 1-pozitsiya -> [0.5, 0.1, -0.3]
- 2-pozitsiya -> [0.4, 0.2, -0.4]

Bu vektorlar token embeddinglari bilan birlashtirilib, modelga so'zlarning ketma-ketligi haqida ma'lumot beradi.

### Token va Position Embeddinglar qanday ishlaydi?

Transformer modellarida token embedding va position embeddinglar birgalikda ishlaydi. Model kirish so'zlarini token embeddinglari orqali vektor shaklida ifodalaydi. Keyin bu vektorlarga position embeddinglar qo'shiladi, bu esa so'zlarning ketma-ketlikdagi o'rnini modelga bildiradi.

Oddiy ko'rinishda jarayon shunday amalga oshadi:

1. **Token embeddinglar**: Har bir so'z yoki token vektorlar yordamida ifodalanadi.
2. **Position embeddinglar**: Har bir so'z yoki tokenning ketma-ketlikdagi pozitsiyasi vektor shaklida ifodalanadi.
3. **Kombinatsiya**: Token va position embeddinglar yig'indisi modelga kiritiladi.

Misol uchun, "Men mushukni yaxshi ko'raman" jumlasi uchun:

- "Men" -> Token embedding: [0.1, 0.3, -0.2]
- Pozitsion embedding: [0.5, 0.1, -0.3]
- Kombinatsiya: [0.6, 0.4, -0.5]

Bu jarayon orqali transformer modeli nafaqat so'zlar orasidagi aloqani, balki ularning ketma-ketlikdagi o'rnini ham hisobga oladi.

### Nima vazifani bajaradi?

- **Token embeddinglar** so'zlarni neyron tarmoqqa tushunarli raqamli ifodalarga aylantiradi. Bu ifodalar o'qitish jarayonida so'zlarning semantik aloqalarini hisobga oladi.
- **Position embeddinglar** so'zlarning ketma-ketlikdagi pozitsiyalarini hisobga oladi, bu esa transformer modellarida so'zlar o'rtasidagi munosabatlarni tushunishda muhimdir.

Yakuniy natijada, token va position embeddinglar transformer modellariga so'zlarning ma'nosini va ularning o'zaro bog'liqligini tushunishga yordam beradi.


In [35]:
class Embedings(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.token_embedings = nn.Embedding(config.vocab_size, config.hidden_size)
        self.position_embedings = nn.Embedding(config.max_position_embeddings, config.hidden_size)
        self.layer_norm = nn.LayerNorm(config.hidden_size, eps=1e-12)
        self.dropout = nn.Dropout()
        
    def forward(self, input_ids):
        seq_length =  input_ids.size(1)
        position_ids = torch.arange(seq_length, dtype=torch.long).unsqueeze(0)
        token_embedings = self.token_embedings(input_ids)
        position_embedings = self.position_embedings(position_ids)
        embedings = token_embedings + position_embedings
        embedings = self.layer_norm(embedings)
        embedings = self.dropout(embedings)
        return embedings

In [36]:
embedings = Embedings(config)
embedings(inputs.input_ids).size()

torch.Size([1, 5, 768])

In [37]:
class TransformerEncoder(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.embedings = Embedings(config)
        self.layers = nn.ModuleList(TransformerEncoderLayer(config) for _ in range(config.num_hidden_layers))
    
    def forward(self, x):
        x = self.embedings(x)
        for layer in self.layers:
            x = layer(x)
        return x

In [38]:
encoder = TransformerEncoder(config)
encoder(inputs.input_ids).size()

torch.Size([1, 5, 768])

In [39]:
class TransformerForSequenceClassification(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.encoder = TransformerEncoder(config)
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        self.classifier = nn.Linear(config.hidden_size, config.num_labels)
    
    def forward(self, x):
        x = self.encoder(x)[:, 0 , :]
        x = self.dropout(x)
        x = self.classifier(x)
        return x

In [40]:
config.num_labels = 3
encoder_classifier = TransformerForSequenceClassification(config)
encoder_classifier(inputs.input_ids).size()

torch.Size([1, 3])

# Transformer Decoder

**Transformer Decoder** — bu Transformer arxitekturasining muhim qismi bo'lib, u kirish (input) ma'lumotlarini qabul qiladi va ularni target (maqsad) ma'lumotlariga aylantiradi. Transformer Decoder asosan ma'lumotlarni tarjima qilish, matn yaratish yoki boshqa target-generatsiya vazifalarida qo'llaniladi.

### Transformer Decoder nima?

Transformer Decoder — bu bir nechta qatlamlardan iborat model, har bir qatlam o'z ichida uchta asosiy komponentni o'z ichiga oladi:

- **Masked Self-Attention Layer (maskalangan o'zaro e'tibor qatlamlari)**
- **Encoder-Decoder Attention Layer (Encoder-Decoder e'tibor qatlamlari)**
- **Feed-Forward Neural Network Layer (oldinga o'tkazuvchi neyron tarmoq qatlamlari)**

Har bir qatlamda kirish ma'lumotlari avvalgi qatlamlar orqali qayta ishlanadi va keyin neyron tarmoq orqali o'tadi. Bu qatlamlar bir necha marta takrorlanadi va natijada maqsadli ma'lumotlar chuqurroq va boyroq vakilliklarga aylanadi.

### Transformer Decoder qanday ishlaydi?

Oddiy qilib aytganda, Transformer Decoder quyidagi bosqichlarda ishlaydi:

1. **Kirish (Input):**
   - Decoder ma'lumotlari ma'lum bir target (maqsad) ma'lumotlardan yoki target-tokenlardan iborat. Dastlab, bu ma'lumotlar token embedding orqali vektor ko'rinishiga o'tkaziladi va pozitsion embeddinglar qo'shiladi.

2. **Masked Self-Attention Layer:**
   - Bu qatlam target ma'lumotlarining har bir qismini o'zaro e'tibor qaratish orqali qayta ishlaydi. Maskalangan self-attention yordamida, model avvalgi target ma'lumotlarga e'tibor qaratadi va keyingi elementlarni o'rgana olmaydi. Bu jarayon modelning target ma'lumotlarni yaratishda o'z-o'zini to'g'ri bashorat qilishiga yordam beradi.

3. **Encoder-Decoder Attention Layer:**
   - Bu qatlam encoderdan olingan vakilliklarga (representations) e'tibor qaratadi. Bu qatlam target ma'lumotlarning encoder tomonidan qayta ishlangan ma'lumotlar bilan qanday bog'liq ekanligini o'rganadi. Masalan, tarjima qilish vazifasida, target so'zlar encoder tomonidan o'rgangan kirish so'zlarga mos keladi.

4. **Feed-Forward Neural Network Layer:**
   - Encoder-Decoder Attention Layer orqali olingan ma'lumotlar keyinroq oldinga o'tkazuvchi neyron tarmoq qatlamlari orqali qayta ishlanadi. Bu qatlam target ma'lumotlarni yanada boy va kontekstual vakillarni hosil qiladi.

5. **Skip Connections va Layer Normalization:**
   - Har bir qatlamda kirish va chiqish ma'lumotlari o'rtasida "skip connections" (uzatma bog'lanishlar) qo'shiladi, bu esa o'qitishni barqaror qiladi. Shuningdek, layer normalization (qatlamni normallashtirish) texnikasi yordamida ma'lumotlar o'rtacha qiymatga keltiriladi, bu modelning samarali ishlashiga yordam beradi.

6. **Natija:**
   - Decoder tomonidan qayta ishlangan ma'lumotlar chiqariladi. Bu ma'lumotlar asosan target ma'lumotlarining kontekstual vakillari bo'lib, ular keyingi bosqichlarda (masalan, so'zlarning ehtimolliklarini hisoblash yoki matn yaratish) ishlatilishi mumkin.

### Transformer Decoderning vazifasi nima?

Transformer Decoderning asosiy vazifasi — target ma'lumotlarni (masalan, tarjima yoki matn yaratish) ishlab chiqarish. Bu jarayon quyidagi vazifalarni bajaradi:

- **Matn yaratish:** Target ma'lumotlarni yaratish, masalan, tarjima qilish yoki yangi matnlarni generatsiya qilish.
- **Kontekstual tushunish:** Target ma'lumotlarning kontekstini chuqurroq tushunadi va o'zaro bog'liqliklarni o'rganadi.
- **E'tibor qaratish:** Encoder tomonidan qayta ishlangan ma'lumotlarga e'tibor qaratish orqali target ma'lumotlarni yanada aniqroq hosil qilish.

Transformer Decoder matn yaratishda yoki tarjima qilishda aniq va samarali natijalar beradigan kuchli komponentdir. Bu jarayon tabiiy tilni qayta ishlash vazifalarida yuqori sifatli ma'lumotlarni ishlab chiqaradi.


In [41]:
seq_len = inputs.input_ids.size(-1)
mask = torch.tril(torch.ones(seq_len, seq_len)).unsqueeze(0)
mask[0]

tensor([[1., 0., 0., 0., 0.],
        [1., 1., 0., 0., 0.],
        [1., 1., 1., 0., 0.],
        [1., 1., 1., 1., 0.],
        [1., 1., 1., 1., 1.]])

In [42]:
scores.masked_fill(mask == 0, -float("inf"))

tensor([[[29.2261,    -inf,    -inf,    -inf,    -inf],
         [-0.3752, 29.0898,    -inf,    -inf,    -inf],
         [-0.7820,  0.8859, 28.8051,    -inf,    -inf],
         [ 0.2877, -1.3409, -0.2578, 24.4738,    -inf],
         [-0.3918,  1.1091,  1.2687, -0.8188, 27.2574]]],
       grad_fn=<MaskedFillBackward0>)

In [43]:
def scaled_dot_product_attention(query, key, value, mask=None):
    dim_k = query.size(-1)
    scores = torch.bmm(query, key.transpose(1, 2)) / sqrt(dim_k)
    if mask is not None:
        scores = scores.masked_fill(mask == 0, float("-inf"))
    weights = F.softmax(scores, dim=-1)
    return weights.bmm(value)